In [178]:
from __future__ import division, print_function
import warnings
warnings.filterwarnings('ignore')
import numpy as np
import pandas as pd
from sklearn.metrics import roc_auc_score

from gensim.models import word2vec

In [179]:
train_df = pd.read_csv('data/train_sessions.csv', parse_dates=['time%s' % i for i in range(1,11)])
test_df = pd.read_csv('data/test_sessions.csv', parse_dates=['time%s' % i for i in range(1,11)])

In [180]:
train_df = train_df.sort_values('time1')

In [181]:
train_df

session_id  site1               time1   site2               time2  \
21668        21669     56 2013-01-12 08:05:57    55.0 2013-01-12 08:05:57   
54842        54843     56 2013-01-12 08:37:23    55.0 2013-01-12 08:37:23   
77291        77292    946 2013-01-12 08:50:13   946.0 2013-01-12 08:50:14   
114020      114021    945 2013-01-12 08:50:17   948.0 2013-01-12 08:50:17   
146669      146670    947 2013-01-12 08:50:20   950.0 2013-01-12 08:50:20   
242170      242171    952 2013-01-12 08:50:22   947.0 2013-01-12 08:50:23   
57156        57157    953 2013-01-12 08:50:25   947.0 2013-01-12 08:50:26   
240200      240201    946 2013-01-12 08:50:28   947.0 2013-01-12 08:50:28   
210685      210686    946 2013-01-12 08:50:31   956.0 2013-01-12 08:50:32   
98803        98804    948 2013-01-12 08:50:37   946.0 2013-01-12 08:50:37   
113493      113494     52 2013-01-12 08:51:05    52.0 2013-01-12 08:51:27   
223836      223837    513 2013-01-12 08:51:36  1116.0 2013-01-12 08:51:36   
145474      145475   4222 2013-01-12 08:52:27  3358.0 2013-01-12 08:52:28   
186632      186633  38667 2013-01-12 08:53:09   181.0 2013-01-12 08:53:09   
45192        45193     56 2013-01-12 08:53:25    55.0 2013-01-12 08:53:26   
102929      102930    570 2013-01-12 08:55:10    23.0 2013-01-12 08:55:11   
15788        15789    820 2013-01-12 08:59:34   820.0 2013-01-12 08:59:36   
205867      205868     48 2013-01-12 09:10:04    56.0 2013-01-12 09:31:21   
21101        21102   5898 2013-01-12 09:14:59  5898.0 2013-01-12 09:15:00   
193453      193454   2570 2013-01-12 09:15:38  2570.0 2013-01-12 09:15:39   
252923      252924     22 2013-01-12 09:20:03    39.0 2013-01-12 09:20:03   
12712        12713    177 2013-01-12 09:23:33   178.0 2013-01-12 09:23:33   
182015      182016     56 2013-01-12 09:25:03    55.0 2013-01-12 09:25:04   
55749        55750     56 2013-01-12 09:37:32    55.0 2013-01-12 09:37:32   
237108      237109     56 2013-01-12 09:56:03    55.0 2013-01-12 09:56:03   
120125      120126   4277 2013-01-12 10:02:11   342.0 2013-01-12 10:02:11   
140104      140105    733 2013-01-12 10:02:46    49.0 2013-01-12 10:04:02   
129356      129357    753 2013-01-12 10:05:08   532.0 2013-01-12 10:05:08   
136698      136699    733 2013-01-12 10:05:32   733.0 2013-01-12 10:05:33   
113188      113189  38668 2013-01-12 10:06:19   733.0 2013-01-12 10:06:34   
...            ...    ...                 ...     ...                 ...   
131401      131402     23 2014-04-30 16:54:28    21.0 2014-04-30 16:54:33   
72348        72349    229 2014-04-30 16:57:08   880.0 2014-04-30 16:57:09   
181939      181940     38 2014-04-30 16:57:26    80.0 2014-04-30 16:58:00   
67430        67431   6003 2014-04-30 17:04:42  6003.0 2014-04-30 17:04:53   
133255      133256     75 2014-04-30 17:06:42   617.0 2014-04-30 17:06:42   
78515        78516     23 2014-04-30 17:06:45    76.0 2014-04-30 17:06:46   
159244      159245     77 2014-04-30 17:06:49    80.0 2014-04-30 17:06:54   
6102          6103     78 2014-04-30 17:06:55    76.0 2014-04-30 17:06:56   
126231      126232     78 2014-04-30 17:07:01    22.0 2014-04-30 17:07:12   
62542        62543    270 2014-04-30 17:07:19   270.0 2014-04-30 17:07:20   
122172      122173  10747 2014-04-30 17:07:36  4890.0 2014-04-30 17:07:36   
182722      182723     21 2014-04-30 17:10:08   229.0 2014-04-30 17:10:08   
216795      216796     77 2014-04-30 17:10:46    77.0 2014-04-30 17:11:04   
88872        88873     76 2014-04-30 17:11:09    80.0 2014-04-30 17:11:09   
201959      201960     78 2014-04-30 17:11:19   881.0 2014-04-30 17:11:19   
99917        99918     77 2014-04-30 17:14:44   812.0 2014-04-30 17:14:45   
35922        35923     76 2014-04-30 17:15:24    81.0 2014-04-30 17:15:24   
91325        91326     76 2014-04-30 17:15:30   816.0 2014-04-30 17:15:32   
182877      182878     22 2014-04-30 17:18:43    81.0 2014-04-30 17:20:12   
36911        36912     80 2014-04-30 17:24:43    80.0 2014-04-30 17:24:53   
1014

In [182]:
sites = ['site%s' % i for i in range(1,11)]
train_df[sites] = train_df[sites].fillna(0).astype('int').astype('str')
test_df[sites] = test_df[sites].fillna(0).astype('int').astype('str')

In [183]:
train_df['list'] = train_df['site1']
test_df['list'] = test_df['site1']
for s in sites[1:]:
    train_df['list'] = train_df['list'] + "," + train_df[s]
    test_df['list'] = test_df['list'] + "," + test_df[s]
train_df['list_w'] = train_df['list'].apply(lambda x: x.split(','))
test_df['list_w'] = test_df['list'].apply(lambda x: x.split(','))

In [184]:
train_df['list_w'].head()

21668                      [56, 55, 0, 0, 0, 0, 0, 0, 0, 0]
54842                    [56, 55, 56, 55, 0, 0, 0, 0, 0, 0]
77291     [946, 946, 951, 946, 946, 945, 948, 784, 949, ...
114020    [945, 948, 949, 948, 945, 946, 947, 945, 946, ...
146669    [947, 950, 948, 947, 950, 952, 946, 951, 946, ...
Name: list_w, dtype: object

In [185]:
test_df['target'] = -1
data = pd.concat([train_df, test_df])

dim_size = 300
model = word2vec.Word2Vec(data['list_w'], size=dim_size, window=3, workers=8)

w2v = dict(zip(model.wv.index2word, model.wv.syn0))

In [8]:
w2v

{'0': array([ 2.88853794e-01, -2.39487052e-01,  5.82235754e-01, -5.34017444e-01,
        -8.33681598e-02, -7.30478391e-02,  3.59761417e-01, -6.62167668e-02,
        -2.25520562e-02,  1.76802546e-01, -2.39671722e-01,  1.65385306e-01,
         1.43585369e-01,  2.13239297e-01, -1.29598886e-01, -6.19116962e-01,
         4.85546768e-01,  2.60417819e-01,  7.38705918e-02,  3.03733107e-02,
         4.01519723e-02, -1.51027873e-01, -3.59796733e-01,  4.68270630e-01,
        -2.34634787e-01, -1.94008410e-01, -9.10860449e-02, -6.43266797e-01,
         2.75405407e-01,  1.57662854e-01, -1.40204355e-01, -2.83746362e-01,
        -5.37590384e-02,  9.23917055e-01, -9.24859121e-02,  4.21201698e-02,
         5.47993541e-01, -2.18054608e-01, -2.55811572e-01,  3.65168661e-01,
         6.50071129e-02, -1.39765963e-01, -7.40110204e-02, -1.66828364e-01,
        -6.89794309e-03, -3.71942282e-01, -3.15441079e-02,  1.97025966e-02,
         5.18049784e-02,  1.84212983e-01, -4.63809669e-02, -9.47821259e-01,
       

In [30]:
len(w2v)

17080

In [34]:
len(next(iter(w2v.values())))

300

In [195]:
class mean_vectorizer(object):
    def __init__(self, word2vec):
        self.word2vec = word2vec
        self.dim = len(next(iter(w2v.values())))
        
    def fit(self, X):
        return self
    
    def transform(self, X):
        return np.array([
            np.mean([self.word2vec.get(w, np.zeros(self.dim)) for w in words], axis=0)
            for words in X
        ])

In [212]:
data_mean = mean_vectorizer(w2v).transform(train_df['list_w'])
data_mean.shape

(253561, 300)

In [ ]:
w2v.values()

In [152]:
data_mean = np.array([
            np.mean([w2v.get(w, np.zeros(dim_size)) for w in words], axis=0)
            for words in train_df['list_w']
        ])
data_mean.shape

(253561, 300)

In [197]:
def split(train, y, ratio):
    idx = round(train.shape[0] * ratio)
    return train[:idx, :], train[idx:, :], y[:idx], y[idx:]

y = train_df['target']
X_train, X_val, y_train, y_val = split(data_mean, y, 0.8)
# xtr.shape, xval.shape, np.mean(ytr), np.mean(yval)

In [198]:
from keras.models import Sequential, Model
from keras.layers import Dense, Dropout, Activation, Input
from keras.preprocessing.text import Tokenizer
from keras import regularizers

In [155]:
model = Sequential()
model.add(Dense(128, input_dim=X_train.shape[1]))
model.add(Activation('relu'))
model.add(Dropout(0.5))
model.add(Dense(1))
model.add(Activation('sigmoid'))
model.compile(loss='binary_crossentropy',
              optimizer='adam',
              metrics=['binary_accuracy'])

In [156]:
history = model.fit(X_train, y_train,
                   batch_size=128,
                   epochs=10,
                   validation_data=(X_val, y_val),
                   class_weight='auto',
                   verbose=0)

In [157]:
preds = model.predict(X_val, batch_size=128)
roc_auc_score(y_val, preds)

0.922247035841377

In [161]:
import xgboost as xgb

In [162]:
d_train = xgb.DMatrix(X_train, label=y_train, missing=np.nan)
d_val = xgb.DMatrix(X_val, label=y_val, missing=np.nan)
watchlist = [(d_train, 'train'), (d_val, 'test')]
history = dict()

In [170]:
params = {
    'max_depth': 26,
    'eta': 0.025,
    'nthread': 8,
    'gamma' : 1,
    'lambda' : 1,
    'subsample': 0.85,
    'eval_metric': ['auc'],
    'objective': 'binary:logistic',
    'colsample_bytree': 0.9,
    'min_child_weight': 100,
    'scale_pos_weight':(1)/y.mean(),
    'seed':7,
    'silent': 1
}

In [171]:
model_new = xgb.train(params,
                     d_train,
                     num_boost_round=200,
                     evals=watchlist,
                     evals_result=history,
                     verbose_eval=20,
                     )

[0]	train-auc:0.957663	test-auc:0.854166
[20]	train-auc:0.989933	test-auc:0.914049
[40]	train-auc:0.992448	test-auc:0.918784
[60]	train-auc:0.993995	test-auc:0.924102
[80]	train-auc:0.995162	test-auc:0.925433
[100]	train-auc:0.995929	test-auc:0.925149
[120]	train-auc:0.996527	test-auc:0.925773
[140]	train-auc:0.997001	test-auc:0.92651
[160]	train-auc:0.997381	test-auc:0.927333
[180]	train-auc:0.997706	test-auc:0.927625
[199]	train-auc:0.997972	test-auc:0.927405


In [213]:
from sklearn.linear_model import LogisticRegression

def get_auc_lr_valid(X, y, C=1, seed=7, ratio=0.8):
    idx = round(X.shape[0] * ratio)
    logit = LogisticRegression(C=C, random_state=seed, n_jobs=-1)
    logit.fit(X[:idx,:], y[:idx])
    preds = logit.predict_proba(X[idx:,:])[:, 1]
    return roc_auc_score(y[idx:], preds)

get_auc_lr_valid(data_mean, y, C=1, seed=17, ratio=0.8)

0.9023000344487273

Weighted mean

In [214]:
from sklearn.feature_extraction.text import TfidfVectorizer
from collections import defaultdict

class tfidf_vectorizer(object):
    def __init__(self, word2vec):
        self.word2vec = word2vec
        self.word2weight = None
        self.dim = dim_size
        
    def fit(self, X):
        tfidf = TfidfVectorizer(analyzer=lambda x: x)
        tfidf.fit(X)
        max_idf = max(tfidf.idf_)
        self.word2weight = defaultdict(
            lambda: max_idf,
            [(w, tfidf.idf_[i]) for w, i in tfidf.vocabulary_.items()])
        return self
    
    def transform(self, X):
        return np.array([
            np.mean([self.word2vec.get(w, np.zeros(self.dim)) * self.word2weight.get(w, np.zeros(self.dim)) 
                    for w in words], axis=0)
            for words in X
        ])
        

In [215]:
data_mean_tfidf = tfidf_vectorizer(w2v).fit(train_df['list_w']).transform(train_df['list_w'])

In [218]:
data_mean_tfidf.shape

(253561, 300)

In [219]:
get_auc_lr_valid(data_mean_tfidf, y, C=1, seed=17, ratio=0.8)

0.9164033703399889